In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

pd.set_option("display.max_columns", 5000)

pd.set_option("display.max_rows", 10000)

In [2]:
full_df = pd.read_csv("CleanedDataset.csv", sep = "|")

In [6]:
philly_df = pd.read_csv("CleanedDataset_Philly.csv", sep = "|")

/Users/shwetachopra/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3147: DtypeWarning: Columns (13) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [14]:
full_df['source'] = 'all'
philly_df['source'] = 'Philadelphia'

In [15]:
full_df.shape

(331553, 42)

In [16]:
philly_df.shape

(64951, 42)

In [3]:
county_court_mapping = pd.read_csv("County_Courts_Mapping.csv")
county_court_mapping['CourtCode_without_hyphen'] = county_court_mapping.CourtCode_without_hyphen.astype(str)
county_court_mapping['county'] = county_court_mapping['COUNTY']
county_court_mapping['DistrictCourtNumber'] = county_court_mapping['DISTRICT COURT'].apply(lambda x:
                                                                                          (str(x).split("-")[0] +\
                                                                                          str(x).split("-")[1][:1].lstrip("0") + \
                                                                                        str(x).split("-")[1][1:] + \
                                                                                          str(x).split("-")[2]).lstrip("0"))

county_court_mapping['DistrictCourtNumber'] = county_court_mapping['DistrictCourtNumber'].astype(int)


In [17]:
full_df = pd.concat([full_df, philly_df])

### Format df

In [40]:
df = full_df.groupby('OTN').first().reset_index()
df['BailPosted'] = df.BailPostingStatus.apply(lambda x: 1 if x == 'Posted' else 0)
df['PartialBailPosted'] = df.BailPostingStatus.apply(lambda x: 1 if x == 'Partial Posting' else 0)
df['BailNotPosted'] = df.BailPostingStatus.apply(lambda x: 1 if pd.isnull(x) else 0)
df['DistrictCourtNumber'] = df['DistrictCourtNumber'].apply(lambda x: -1 if pd.isnull(x) else x)
df['DistrictCourtNumber'] = df['DistrictCourtNumber'].astype(int)
df = df.merge(county_court_mapping[['county', 'CountyCode', 'DistrictCourtNumber']], 
              on = 'DistrictCourtNumber', 
              how = 'left')
df['county'] = df.apply(lambda x: x['county'] if not pd.isnull(x['county']) else \
                        'Lancaster' if x['DistrictCourtNumber'] == 2000 else \
                       'Allegheny' if x['DistrictCourtNumber'] == 5003 else \
                       'Fayette', axis = 1)
df['CountyCode'] = df.apply(lambda x: x['CountyCode'] if not pd.isnull(x['CountyCode']) else \
                        36 if x['DistrictCourtNumber'] == 2000 else \
                       2 if x['DistrictCourtNumber'] == 5003 else \
                       26, axis = 1)
df['DefendantRace'] = df['DefendantRace'].apply(lambda x: 'Missing' if pd.isnull(x) else x)
df['charge'] = df.Description.apply(lambda x : str(x).lower().strip())
df['county'] = df.apply(lambda x: x['county'] if x['source'] == 'all' else x['source'], axis = 1)
df['CountyCode'] = df.apply(lambda x: x['CountyCode'] if x['source'] == 'all' else 51, axis = 1)

In [41]:
df['DefendantRace'].value_counts()

White                               253295
Black                               116791
Missing                               5648
Unknown/Unreported                    4175
Asian/Pacific Islander                1591
Asian                                 1364
Native American/Alaskan Native         284
Bi-Racial                              155
Native Hawaiian/Pacific Islander        14
Name: DefendantRace, dtype: int64

In [42]:
# Only run when analyzing cases where Bail is yet to be Posted
#df = df[df.BailNotPosted == 1]

### Analysis Functions

In [43]:
def percentile(n):
    def percentile_(x):
        return np.percentile(x, n)
    percentile_.__name__ = 'percentile_%s' % n
    return percentile_

def mean_minus_99th_percentile(x):
    cap = np.percentile(x, 99)
    new_x = [cap if element > cap else element for element in x ]
    return np.mean(new_x)
    

### Analysis Tables

#### Statewide Summary

In [44]:
statewide_summary = df.groupby("BailType").agg({
    'BailActionAmount': ['mean', mean_minus_99th_percentile, 'median', percentile(25), percentile(75)],
    'BailPosted': 'sum',
    'PartialBailPosted': 'sum',
    'BailNotPosted': 'sum',
    'OTN': 'count'
}
).reset_index()

statewide_summary.columns = ['_'.join(col).strip() for col in statewide_summary.columns.values]
statewide_summary.columns = [
    'BailType',
    'BailActionAmtMean',
    'BailActionAmtMeanCapped99th',
    'BailActionAmtMedian',
    'BailActionAmtQ1',
    'BailActionAmtQ3',
    'BailPosted',
    'PartialBailPosted',
    'BailNotPosted',
    'OTN'
    
]

statewide_summary['BailPostedShare'] = statewide_summary.BailPosted/statewide_summary.OTN
statewide_summary['PartialBailPostedShare'] = statewide_summary.PartialBailPosted/statewide_summary.OTN
statewide_summary['BailNotPostedShare'] = statewide_summary.BailNotPosted/statewide_summary.OTN
statewide_summary['ShareOfCases'] = statewide_summary.OTN/statewide_summary.OTN.sum()
statewide_summary = statewide_summary.rename(columns= {
    'BailType': 'BailType',
    'OTN' : 'NumberOfCases',
    'ShareOfCases': 'ShareOfCases',
    'BailPostedShare': 'BailPostedRatio',
    'PartialBailPostedShare': 'PartialBailPostedRatio',
    'BailNotPostedShare': 'BailNotPostedRatio',    
    'BailPosted': 'BailPostedCases',
    'PartialBailPosted': 'PartialBailPostedCases',
    'BailNotPosted': 'BailNotPostedCases',
  
})
statewide_summary = statewide_summary[['BailType', 'NumberOfCases', 'ShareOfCases',
                                          'BailActionAmtMean', 'BailActionAmtMeanCapped99th', 'BailActionAmtMedian',
                                       'BailActionAmtQ1', 'BailActionAmtQ3',
                                       'BailPostedRatio', 'BailPostedCases', 'PartialBailPostedRatio', 
                                       'PartialBailPostedCases', 'BailNotPostedRatio', 'BailNotPostedCases']]

In [45]:
statewide_summary

BailType  NumberOfCases  ShareOfCases  BailActionAmtMean  \
0     Monetary         166299      0.433842       46010.474765   
1      Nominal            396      0.001033        3655.076111   
2  Nonmonetary          24203      0.063141           0.000000   
3          ROR          86149      0.224746           0.000000   
4    Unsecured         106270      0.277238        8473.557585   

   BailActionAmtMeanCapped99th  BailActionAmtMedian  BailActionAmtQ1  \
0                 38432.918616              10000.0           5000.0   
1                  2076.793283                  1.0              1.0   
2                     0.000000                  0.0              0.0   
3                     0.000000                  0.0              0.0   
4                  7837.884300               5000.0           2500.0   

   BailActionAmtQ3  BailPostedRatio  BailPostedCases  PartialBailPostedRatio  \
0          30000.0         0.403953            67177                0.007787   
1              1.0         0.310606              123                0.005051   
2              0.0         0.062472             1512                0.000661   
3              0.0         0.114720             9883                0.000209   
4          10000.0         0.398645            42364                0.001694   

   PartialBailPostedCases  BailNotPostedRatio  BailNotPostedCases  
0                    1295            0.588236               97823  
1                       2            0.684343                 271  
2                      16            0.936867               22675  
3                      18            0.885071               76248  
4                     180            0.599661               63726

#### State x Race

In [46]:
statewide_race_summary = df.groupby(["DefendantRace", "BailType"]).agg({
    'BailActionAmount': ['mean', mean_minus_99th_percentile, 'median', percentile(25), percentile(75)],
    'BailPosted': 'sum',
    'PartialBailPosted': 'sum',
    'BailNotPosted': 'sum',
    'OTN': 'count'
}
).reset_index()

statewide_race_summary.columns = ['_'.join(col).strip() for col in statewide_race_summary.columns.values]
statewide_race_summary.columns = [
    'DefendantRace',
    'BailType',
    'BailActionAmtMean',
    'BailActionAmtMeanCapped99th',
    'BailActionAmtMedian',
    'BailActionAmtQ1',
    'BailActionAmtQ3',
    'BailPosted',
    'PartialBailPosted',
    'BailNotPosted',
    'OTN'
    
]

statewide_race_totals = df.groupby("DefendantRace").OTN.count().reset_index()
statewide_race_totals.columns = ['DefendantRace', 'total_cases']
statewide_race_summary = statewide_race_summary.merge(statewide_race_totals, on = "DefendantRace", how = 'left')

statewide_race_summary['BailPostedShare'] = statewide_race_summary.BailPosted/statewide_race_summary.OTN
statewide_race_summary['PartialBailPostedShare'] = statewide_race_summary.PartialBailPosted/statewide_race_summary.OTN
statewide_race_summary['BailNotPostedShare'] = statewide_race_summary.BailNotPosted/statewide_race_summary.OTN
statewide_race_summary['ShareOfCases'] = statewide_race_summary.OTN/statewide_race_summary.total_cases
statewide_race_summary = statewide_race_summary.rename(columns= {
    'BailType': 'BailType',
    'OTN' : 'NumberOfCasesOfType',
    'total_cases' : 'NumberOfCasesAllTypes',
    'ShareOfCases': 'ShareOfCases',
    'BailPostedShare': 'BailPostedRatio',
    'PartialBailPostedShare': 'PartialBailPostedRatio',
    'BailNotPostedShare': 'BailNotPostedRatio',    
    'BailPosted': 'BailPostedCases',
    'PartialBailPosted': 'PartialBailPostedCases',
    'BailNotPosted': 'BailNotPostedCases',
})
statewide_race_summary = statewide_race_summary[['DefendantRace', 'BailType', 'NumberOfCasesAllTypes', 'NumberOfCasesOfType', 'ShareOfCases',
                                      'BailActionAmtMean', 'BailActionAmtMeanCapped99th', 'BailActionAmtMedian',
                                       'BailActionAmtQ1', 'BailActionAmtQ3',
                                 'BailPostedRatio', 
                                       'BailPostedCases', 'PartialBailPostedRatio', 'PartialBailPostedCases',
                                'BailNotPostedRatio', 'BailNotPostedCases']]

In [47]:
statewide_race_summary

DefendantRace     BailType  NumberOfCasesAllTypes  \
0                              Asian     Monetary                   1364   
1                              Asian  Nonmonetary                   1364   
2                              Asian          ROR                   1364   
3                              Asian    Unsecured                   1364   
4             Asian/Pacific Islander     Monetary                   1591   
5             Asian/Pacific Islander      Nominal                   1591   
6             Asian/Pacific Islander  Nonmonetary                   1591   
7             Asian/Pacific Islander          ROR                   1591   
8             Asian/Pacific Islander    Unsecured                   1591   
9                          Bi-Racial     Monetary                    155   
10                         Bi-Racial  Nonmonetary                    155   
11                         Bi-Racial          ROR                    155   
12                         Bi-Racial    Unsecured                    155   
13                             Black     Monetary                 116791   
14                             Black      Nominal                 116791   
15                             Black  Nonmonetary                 116791   
16                             Black          ROR                 116791   
17                             Black    Unsecured                 116791   
18                           Missing     Monetary                   5648   
19                           Missing      Nominal                   5648   
20                           Missing  Nonmonetary                   5648   
21                           Missing          ROR                   5648   
22                           Missing    Unsecured                   5648   
23    Native American/Alaskan Native     Monetary                    284   
24    Native American/Alaskan Native  Nonmonetary                    284   
25    Native American/Alaskan Native          ROR                    284   
26    Native American/Alaskan Native    Unsecured                    284   
27  Native Hawaiian/Pacific Islander     Monetary                     14   
28  Native Hawaiian/Pacific Islander  Nonmonetary                     14   
29  Native Hawaiian/Pacific Islander          ROR                     14   
30  Native Hawaiian/Pacific Islander    Unsecured                     14   
31                Unknown/Unreported     Monetary                   4175   
32                Unknown/Unreported      Nominal                   4175   
33                Unknown/Unreported  Nonmonetary                   4175   
34                Unknown/Unreported          ROR                   4175   
35                Unknown/Unreported    Unsecured                   4175   
36                             White     Monetary                 253295   
37                             White      Nominal                 253295   
38                             White  Nonmonetary                 253295   
39                             White          ROR                 253295   
40                             White    Unsecured                 253295   

    NumberOfCasesOfType  ShareOfCases  BailActionAmtMean  \
0                   389      0.285191       50931.917738   
1                    25      0.018328           0.000000   
2                   369      0.270528           0.000000   
3                   581      0.425953       12026.335628   
4                   665      0.417976       61427.126316   
5                     1      0.000629           1.000000   
6                   149      0.093652           0.000000   
7                   539      0.338781           0.000000   
8                   237      0.148963        7093.248945   
9                    57      0.367742       48640.350877   
10                    5      0.032258           0.000000   
11                   36      0.232258           0.000000   
12                   57      0.367742        8298.

#### State x Charge

In [48]:
final_charge_list = [
    'simple assault',
    'manufacture, delivery, or possession with intent to manufacture or deliver',
    'retail theft-take mdse',
    'aggravated assault',
    'int poss contr subst by per not reg',
    'dui: gen imp/inc of driving safely - 1st off',
    'theft by unlaw taking-movable prop',
    'receiving stolen property',
    'marijuana-small amt personal use',
    'poss of marijuana'
]

In [49]:
statewide_charge_summary = df[df.charge.isin(final_charge_list)]
statewide_charge_summary = statewide_charge_summary.groupby(["charge", "BailType"]).agg({
    'BailActionAmount': ['mean', mean_minus_99th_percentile, 'median', percentile(25), percentile(75)],
    'BailPosted': 'sum',
    'PartialBailPosted': 'sum',
    'BailNotPosted': 'sum',
    'OTN': 'count'
}
).reset_index()

statewide_charge_summary.columns = ['_'.join(col).strip() for col in statewide_charge_summary.columns.values]
statewide_charge_summary.columns = [
    'charge',
    'BailType',
    'BailActionAmtMean',
    'BailActionAmtMeanCapped99th',
    'BailActionAmtMedian',
    'BailActionAmtQ1',
    'BailActionAmtQ3',
    'BailPosted',
    'PartialBailPosted',
    'BailNotPosted',
    'OTN'
    
]

statewide_charge_totals = df.groupby("charge").OTN.count().reset_index()
statewide_charge_totals.columns = ['charge', 'total_cases']
statewide_charge_summary = statewide_charge_summary.merge(statewide_charge_totals, on = "charge", how = 'left')

statewide_charge_summary['BailPostedShare'] = statewide_charge_summary.BailPosted/statewide_charge_summary.OTN
statewide_charge_summary['PartialBailPostedShare'] = statewide_charge_summary.PartialBailPosted/statewide_charge_summary.OTN
statewide_charge_summary['BailNotPostedShare'] = statewide_charge_summary.BailNotPosted/statewide_charge_summary.OTN
statewide_charge_summary['ShareOfCases'] = statewide_charge_summary.OTN/statewide_charge_summary.total_cases
statewide_charge_summary = statewide_charge_summary.rename(columns= {
    'BailType': 'BailType',
    'OTN' : 'NumberOfCasesOfType',
    'total_cases' : 'NumberOfCasesAllTypes',
    'ShareOfCases': 'ShareOfCases',
    'BailPostedShare': 'BailPostedRatio',
    'PartialBailPostedShare': 'PartialBailPostedRatio',
    'BailNotPostedShare': 'BailNotPostedRatio',    
    'BailPosted': 'BailPostedCases',
    'PartialBailPosted': 'PartialBailPostedCases',
    'BailNotPosted': 'BailNotPostedCases',
})
statewide_charge_summary = statewide_charge_summary[['charge', 'BailType', 'NumberOfCasesAllTypes', 'NumberOfCasesOfType', 'ShareOfCases',
                                      'BailActionAmtMean', 'BailActionAmtMeanCapped99th', 'BailActionAmtMedian',
                                       'BailActionAmtQ1', 'BailActionAmtQ3',
                                 'BailPostedRatio', 
                                       'BailPostedCases', 'PartialBailPostedRatio', 'PartialBailPostedCases',
                                'BailNotPostedRatio', 'BailNotPostedCases']]

In [50]:
statewide_charge_summary

charge     BailType  \
0                                  aggravated assault     Monetary   
1                                  aggravated assault      Nominal   
2                                  aggravated assault  Nonmonetary   
3                                  aggravated assault          ROR   
4                                  aggravated assault    Unsecured   
5        dui: gen imp/inc of driving safely - 1st off     Monetary   
6        dui: gen imp/inc of driving safely - 1st off      Nominal   
7        dui: gen imp/inc of driving safely - 1st off  Nonmonetary   
8        dui: gen imp/inc of driving safely - 1st off          ROR   
9        dui: gen imp/inc of driving safely - 1st off    Unsecured   
10                int poss contr subst by per not reg     Monetary   
11                int poss contr subst by per not reg      Nominal   
12                int poss contr subst by per not reg  Nonmonetary   
13                int poss contr subst by per not reg          ROR   
14                int poss contr subst by per not reg    Unsecured   
15  manufacture, delivery, or possession with inte...     Monetary   
16  manufacture, delivery, or possession with inte...      Nominal   
17  manufacture, delivery, or possession with inte...  Nonmonetary   
18  manufacture, delivery, or possession with inte...          ROR   
19  manufacture, delivery, or possession with inte...    Unsecured   
20                   marijuana-small amt personal use     Monetary   
21                   marijuana-small amt personal use      Nominal   
22                   marijuana-small amt personal use  Nonmonetary   
23                   marijuana-small amt personal use          ROR   
24                   marijuana-small amt personal use    Unsecured   
25                                  poss of marijuana     Monetary   
26                                  poss of marijuana      Nominal   
27                                  poss of marijuana  Nonmonetary   
28                                  poss of marijuana          ROR   
29                                  poss of marijuana    Unsecured   
30                          receiving stolen property     Monetary   
31                          receiving stolen property      Nominal   
32                          receiving stolen property  Nonmonetary   
33                          receiving stolen property          ROR   
34                          receiving stolen property    Unsecured   
35                             retail theft-take mdse     Monetary   
36                             retail theft-take mdse      Nominal   
37                             retail theft-take mdse  Nonmonetary   
38                             retail theft-take mdse          ROR   
39                             retail theft-take mdse    Unsecured   
40                                     simple assault     Monetary   
41                                     simple assault      Nominal   
42                                     simple assault  Nonmonetary   
43                                     simple assault          ROR   
44                                     simple assault    Unsecured   
45                 theft by unlaw taking-movable prop     Monetary   
46                 theft by unlaw taking-movable prop      Nominal   
47                 theft by unlaw taking-movable prop  Nonmonetary   
48                 theft by unlaw taking-movable prop          ROR   
49                 theft by unlaw taking-movable prop    Unsecured   

    NumberOfCasesAllTypes  NumberOfCasesOfType  ShareOfCases  \
0                   15373                13068      0.850062   
1                   15373                    6      0.000390   
2                   15373                  624      0.040591   
3                   15373                  210      0.013660   
4                   15373                 1465      0.095297   
5                   40845                 4046      0.099057   
6                   40845   

#### County Summary

In [51]:
county_summary = df.groupby(["county", "BailType"]).agg({
    'BailActionAmount': ['mean', mean_minus_99th_percentile, 'median', percentile(25), percentile(75)],
    'BailPosted': 'sum',
    'PartialBailPosted': 'sum',
    'BailNotPosted': 'sum',
    'OTN': 'count'
}
).reset_index()

county_summary.columns = ['_'.join(col).strip() for col in county_summary.columns.values]
county_summary.columns = [
    'county',
    'BailType',
    'BailActionAmtMean',
    'BailActionAmtMeanCapped99th',
    'BailActionAmtMedian',
    'BailActionAmtQ1',
    'BailActionAmtQ3',
    'BailPosted',
    'PartialBailPosted',
    'BailNotPosted',
    'OTN'
    
]

county_totals = df.groupby("county").OTN.count().reset_index()
county_totals.columns = ['county', 'total_cases']
county_summary = county_summary.merge(county_totals, on = "county", how = 'left')

county_summary['BailPostedShare'] = county_summary.BailPosted/county_summary.OTN
county_summary['PartialBailPostedShare'] = county_summary.PartialBailPosted/county_summary.OTN
county_summary['BailNotPostedShare'] = county_summary.BailNotPosted/county_summary.OTN
county_summary['ShareOfCases'] = county_summary.OTN/county_summary.total_cases
county_summary = county_summary.rename(columns= {
    'BailType': 'BailType',
    'OTN' : 'NumberOfCasesOfType',
    'total_cases' : 'NumberOfCasesAllTypes',
    'ShareOfCases': 'ShareOfCases',
    'BailPostedShare': 'BailPostedRatio',
    'PartialBailPostedShare': 'PartialBailPostedRatio',
    'BailNotPostedShare': 'BailNotPostedRatio',    
    'BailPosted': 'BailPostedCases',
    'PartialBailPosted': 'PartialBailPostedCases',
    'BailNotPosted': 'BailNotPostedCases',
})
county_summary = county_summary[['county', 'BailType', 'NumberOfCasesAllTypes', 'NumberOfCasesOfType', 'ShareOfCases',
                                      'BailActionAmtMean', 'BailActionAmtMeanCapped99th', 'BailActionAmtMedian',
                                       'BailActionAmtQ1', 'BailActionAmtQ3',
                                 'BailPostedRatio', 
                                       'BailPostedCases', 'PartialBailPostedRatio', 'PartialBailPostedCases',
                                'BailNotPostedRatio', 'BailNotPostedCases']]

In [52]:
county_summary

county     BailType  NumberOfCasesAllTypes  NumberOfCasesOfType  \
0             Adams     Monetary                   2280                  714   
1             Adams  Nonmonetary                   2280                  340   
2             Adams          ROR                   2280                  578   
3             Adams    Unsecured                   2280                  648   
4         Allegheny     Monetary                  47473                20214   
5         Allegheny      Nominal                  47473                   15   
6         Allegheny  Nonmonetary                  47473                13903   
7         Allegheny          ROR                  47473                12075   
8         Allegheny    Unsecured                  47473                 1266   
9         Armstrong     Monetary                   1770                  735   
10        Armstrong  Nonmonetary                   1770                   55   
11        Armstrong          ROR                   1770                  755   
12        Armstrong    Unsecured                   1770                  225   
13           Beaver     Monetary                   5765                 2931   
14           Beaver      Nominal                   5765                    1   
15           Beaver  Nonmonetary                   5765                  117   
16           Beaver          ROR                   5765                 1967   
17           Beaver    Unsecured                   5765                  749   
18          Bedford     Monetary                   1392                  520   
19          Bedford          ROR                   1392                   27   
20          Bedford    Unsecured                   1392                  845   
21            Berks     Monetary                  11330                 5765   
22            Berks      Nominal                  11330                    3   
23            Berks  Nonmonetary                  11330                  100   
24            Berks          ROR                  11330                 1709   
25            Berks    Unsecured                  11330                 3753   
26            Blair     Monetary                   4298                 1324   
27            Blair  Nonmonetary                   4298                    3   
28            Blair          ROR                   4298                   19   
29            Blair    Unsecured                   4298                 2952   
30         Bradford     Monetary                   1773                  814   
31         Bradford  Nonmonetary                   1773                  514   
32         Bradford          ROR                   1773                  206   
33         Bradford    Unsecured                   1773                  239   
34            Bucks     Monetary                  13830                 4823   
35            Bucks      Nominal                  13830                    2   
36            Bucks  Nonmonetary                  13830                   33   
37            Bucks          ROR                  13830                 2201   
38            Bucks    Unsecured                  13830                 6771   
39           Butler     Monetary                   5123                 1820   
40           Butler      Nominal                   5123                   28   
41           Butler  Nonmonetary                   5123                  441   
42           Butler          ROR                   5123                 2511   
43           Butler    Unsecured                   5123                  323   
44          Cambria     Monetary                   4395                 1978   
45          Cambria  Nonmonetary                   4395                    2   
46          Cambria          ROR                   4395                  910   
47          Cambria    Unsecured                   4395                 1505   
48          Cameron     Monetary                    136                   30   
49          C

#### County x Race

In [53]:
county_race_summary = df.groupby(["county", "DefendantRace", "BailType"]).agg({
    'BailActionAmount': ['mean', mean_minus_99th_percentile, 'median', percentile(25), percentile(75)],
    'BailPosted': 'sum',
    'PartialBailPosted': 'sum',
    'BailNotPosted': 'sum',
    'OTN': 'count'
}
).reset_index()

county_race_summary.columns = ['_'.join(col).strip() for col in county_race_summary.columns.values]
county_race_summary.columns = [
    'county',
    'DefendantRace',
    'BailType',
    'BailActionAmtMean',
    'BailActionAmtMeanCapped99th',
    'BailActionAmtMedian',
    'BailActionAmtQ1',
    'BailActionAmtQ3',
    'BailPosted',
    'PartialBailPosted',
    'BailNotPosted',
    'OTN'
    
]

county_race_totals = df.groupby(["county", 'DefendantRace']).OTN.count().reset_index()
county_race_totals.columns = ['county', 'DefendantRace','total_cases']
county_race_summary = county_race_summary.merge(county_race_totals, on = ["county", 'DefendantRace'], how = 'left')

county_race_summary['BailPostedShare'] = county_race_summary.BailPosted/county_race_summary.OTN
county_race_summary['PartialBailPostedShare'] = county_race_summary.PartialBailPosted/county_race_summary.OTN
county_race_summary['BailNotPostedShare'] = county_race_summary.BailNotPosted/county_race_summary.OTN
county_race_summary['ShareOfCases'] = county_race_summary.OTN/county_race_summary.total_cases
county_race_summary = county_race_summary.rename(columns= {
    'BailType': 'BailType',
    'OTN' : 'NumberOfCasesOfType',
    'total_cases' : 'NumberOfCasesAllTypes',
    'ShareOfCases': 'ShareOfCases',
    'BailPostedShare': 'BailPostedRatio',
    'PartialBailPostedShare': 'PartialBailPostedRatio',
    'BailNotPostedShare': 'BailNotPostedRatio',    
    'BailPosted': 'BailPostedCases',
    'PartialBailPosted': 'PartialBailPostedCases',
    'BailNotPosted': 'BailNotPostedCases',
})
county_race_summary = county_race_summary[['county', 'DefendantRace', 'BailType', 'NumberOfCasesAllTypes', 'NumberOfCasesOfType',
                                           'ShareOfCases',
                                      'BailActionAmtMean', 'BailActionAmtMeanCapped99th', 'BailActionAmtMedian',
                                       'BailActionAmtQ1', 'BailActionAmtQ3',
                                           'BailPostedRatio', 
                                       'BailPostedCases', 'PartialBailPostedRatio', 'PartialBailPostedCases',
                                          'BailNotPostedRatio', 'BailNotPostedCases']]

In [54]:
county_race_summary

county                     DefendantRace     BailType  \
0              Adams                             Asian          ROR   
1              Adams                             Asian    Unsecured   
2              Adams            Asian/Pacific Islander     Monetary   
3              Adams            Asian/Pacific Islander    Unsecured   
4              Adams                             Black     Monetary   
5              Adams                             Black  Nonmonetary   
6              Adams                             Black          ROR   
7              Adams                             Black    Unsecured   
8              Adams                           Missing     Monetary   
9              Adams                           Missing  Nonmonetary   
10             Adams                           Missing          ROR   
11             Adams                           Missing    Unsecured   
12             Adams    Native American/Alaskan Native     Monetary   
13             Adams    Native American/Alaskan Native          ROR   
14             Adams    Native American/Alaskan Native    Unsecured   
15             Adams                Unknown/Unreported     Monetary   
16             Adams                Unknown/Unreported  Nonmonetary   
17             Adams                Unknown/Unreported          ROR   
18             Adams                Unknown/Unreported    Unsecured   
19             Adams                             White     Monetary   
20             Adams                             White  Nonmonetary   
21             Adams                             White          ROR   
22             Adams                             White    Unsecured   
23         Allegheny                             Asian  Nonmonetary   
24         Allegheny                             Asian          ROR   
25         Allegheny            Asian/Pacific Islander     Monetary   
26         Allegheny            Asian/Pacific Islander  Nonmonetary   
27         Allegheny            Asian/Pacific Islander          ROR   
28         Allegheny            Asian/Pacific Islander    Unsecured   
29         Allegheny                         Bi-Racial          ROR   
30         Allegheny                             Black     Monetary   
31         Allegheny                             Black      Nominal   
32         Allegheny                             Black  Nonmonetary   
33         Allegheny                             Black          ROR   
34         Allegheny                             Black    Unsecured   
35         Allegheny                           Missing     Monetary   
36         Allegheny                           Missing  Nonmonetary   
37         Allegheny                           Missing          ROR   
38         Allegheny                           Missing    Unsecured   
39         Allegheny    Native American/Alaskan Native     Monetary   
40         Allegheny    Native American/Alaskan Native  Nonmonetary   
41         Allegheny    Native American/Alaskan Native          ROR   
42         Allegheny                Unknown/Unreported     Monetary   
43         Allegheny                Unknown/Unreported  Nonmonetary   
44         Allegheny                Unknown/Unreported          ROR   
45         Allegheny                Unknown/Unreported    Unsecured   
46         Allegheny                             White     Monetary   
47         Allegheny                             White      Nominal   
48         Allegheny                             White  Nonmonetary   
49         Allegheny                             White          ROR   
50         Allegheny                             White    Unsecured   
51         Armstrong                             Asian     Monetary   
52         Armstrong                             Black     Monetary   
53         Armstrong                             Black  Nonmonetary   
54         Armstrong                             Black          ROR   
55         Armstrong                  

#### County x MDJ

In [55]:
mdj_summary = df.groupby(["county", "BailActionAuthority", "BailType"]).agg({
    'BailActionAmount': ['mean', mean_minus_99th_percentile, 'median', percentile(25), percentile(75)],
    'BailPosted': 'sum',
    'PartialBailPosted': 'sum',
    'BailNotPosted': 'sum',
    'OTN': 'count'
}
).reset_index()

mdj_summary.columns = ['_'.join(col).strip() for col in mdj_summary.columns.values]
mdj_summary.columns = [
    "county",
    'BailActionAuthority',
    'BailType',
    'BailActionAmtMean',
    'BailActionAmtMeanCapped99th',
    'BailActionAmtMedian',
    'BailActionAmtQ1',
    'BailActionAmtQ3',
    'BailPosted',
    'PartialBailPosted',
    'BailNotPosted',
    'OTN'
    
]

mdj_totals = df.groupby(["county", "BailActionAuthority"]).OTN.count().reset_index()
mdj_totals.columns = ["county", 'BailActionAuthority', 'total_cases']
mdj_summary = mdj_summary.merge(mdj_totals, on = ["county", "BailActionAuthority"], how = 'left')

mdj_summary['BailPostedShare'] = mdj_summary.BailPosted/mdj_summary.OTN
mdj_summary['PartialBailPostedShare'] = mdj_summary.PartialBailPosted/mdj_summary.OTN
mdj_summary['BailNotPostedShare'] = mdj_summary.BailNotPosted/mdj_summary.OTN
mdj_summary['ShareOfCases'] = mdj_summary.OTN/mdj_summary.total_cases
mdj_summary = mdj_summary.rename(columns= {
    'BailType': 'BailType',
    'OTN' : 'NumberOfCasesOfType',
    'total_cases' : 'NumberOfCasesAllTypes',
    'ShareOfCases': 'ShareOfCases',
    'BailPostedShare': 'BailPostedRatio',
    'PartialBailPostedShare': 'PartialBailPostedRatio',
    'BailNotPostedShare': 'BailNotPostedRatio',    
    'BailPosted': 'BailPostedCases',
    'PartialBailPosted': 'PartialBailPostedCases',
    'BailNotPosted': 'BailNotPostedCases',
})
mdj_summary = mdj_summary[['county', 'BailActionAuthority', 'BailType', 'NumberOfCasesAllTypes', 'NumberOfCasesOfType', 'ShareOfCases',
                                      'BailActionAmtMean', 'BailActionAmtMeanCapped99th', 'BailActionAmtMedian',
                                       'BailActionAmtQ1', 'BailActionAmtQ3',
                                 'BailPostedRatio', 
                                       'BailPostedCases', 'PartialBailPostedRatio', 'PartialBailPostedCases',
                                'BailNotPostedRatio', 'BailNotPostedCases']]

In [56]:
mdj_summary

county                                BailActionAuthority  \
0              Adams                                  Beauchat, Mark D.   
1              Adams                                  Beauchat, Mark D.   
2              Adams                                  Beauchat, Mark D.   
3              Adams                                  Beauchat, Mark D.   
4              Adams                                  Bowman, Daniel S.   
5              Adams                                  Bowman, Daniel S.   
6              Adams                                  Bowman, Daniel S.   
7              Adams                                  Bowman, Daniel S.   
8              Adams                             Harvey, Matthew Robert   
9              Adams                             Harvey, Matthew Robert   
10             Adams                             Harvey, Matthew Robert   
11             Adams                             Harvey, Matthew Robert   
12             Adams                              Haskell, Ronald J Jr.   
13             Adams                                    Little, Tony J.   
14             Adams                                    Little, Tony J.   
15             Adams                                    Little, Tony J.   
16             Adams                                    Little, Tony J.   
17         Allegheny            Allegheny Arraignment Court MDJ 05-0-04   
18         Allegheny            Allegheny Arraignment Court MDJ 05-0-04   
19         Allegheny            Allegheny Arraignment Court MDJ 05-0-04   
20         Allegheny                                    Armour, John W.   
21         Allegheny                                    Armour, John W.   
22         Allegheny                                    Armour, John W.   
23         Allegheny                                    Armour, John W.   
24         Allegheny                                  Arnoni, Ronald A.   
25         Allegheny                                  Arnoni, Ronald A.   
26         Allegheny                                  Arnoni, Ronald A.   
27         Allegheny                                  Arnoni, Ronald A.   
28         Allegheny                                  Arnoni, Ronald A.   
29         Allegheny                                      Arthur, Brian   
30         Allegheny                                  Barner, Joseph K.   
31         Allegheny                                  Barner, Joseph K.   
32         Allegheny                                  Barner, Robert L.   
33         Allegheny                                  Barner, Robert L.   
34         Allegheny                                  Barner, Robert L.   
35         Allegheny                                    Barron, John W.   
36         Allegheny                                   Barton, David J.   
37         Allegheny                                   Barton, David J.   
38         Allegheny                                   Barton, David J.   
39         Allegheny                                    Bates, D. Glenn   
40         Allegheny                                 Bengel, Carolyn S.   
41         Allegheny                                 Bengel, Carolyn S.   
42         Allegheny                                 Bengel, Carolyn S.   
43         Allegheny                                 Bengel, Carolyn S.   
44         Allegheny                            Blaschak, Suzanne Renee   
45         Allegheny                               Bompiani, L. Anthony   
46         Allegheny                               Bompiani, L. Anthony   
47         Allegheny                               Borkowski, Edward J.   
48         Allegheny                                      Bova, John N.   
49         Allegheny                                      Bova, John N.   
50         Allegheny                                      Bova, John N.   
51         Allegheny                                    Brian, David E.   
52         Allegheny                   

#### County x MDJ x Race

In [57]:
mdj_race_summary = df.groupby(["county", "BailActionAuthority", "DefendantRace", "BailType"]).agg({
    'BailActionAmount': ['mean', mean_minus_99th_percentile, 'median', percentile(25), percentile(75)],
    'BailPosted': 'sum',
    'PartialBailPosted': 'sum',
    'BailNotPosted': 'sum',
    'OTN': 'count'
}
).reset_index()

mdj_race_summary.columns = ['_'.join(col).strip() for col in mdj_race_summary.columns.values]
mdj_race_summary.columns = [
    "county",
    'BailActionAuthority',
    "DefendantRace",
    'BailType',
    'BailActionAmtMean',
    'BailActionAmtMeanCapped99th',
    'BailActionAmtMedian',
    'BailActionAmtQ1',
    'BailActionAmtQ3',
    'BailPosted',
    'PartialBailPosted',
    'BailNotPosted',
    'OTN'
    
]

mdj_race_totals = df.groupby(["county", "BailActionAuthority", "DefendantRace"]).OTN.count().reset_index()
mdj_race_totals.columns = ["county", 'BailActionAuthority', "DefendantRace", 'total_cases']
mdj_race_summary = mdj_race_summary.merge(mdj_race_totals, on = ["county", "BailActionAuthority", "DefendantRace"], how = 'left')

mdj_race_summary['BailPostedShare'] = mdj_race_summary.BailPosted/mdj_race_summary.OTN
mdj_race_summary['PartialBailPostedShare'] = mdj_race_summary.PartialBailPosted/mdj_race_summary.OTN
mdj_race_summary['BailNotPostedShare'] = mdj_race_summary.BailNotPosted/mdj_race_summary.OTN
mdj_race_summary['ShareOfCases'] = mdj_race_summary.OTN/mdj_race_summary.total_cases
mdj_race_summary = mdj_race_summary.rename(columns= {
    'BailType': 'BailType',
    'OTN' : 'NumberOfCasesOfType',
    'total_cases' : 'NumberOfCasesAllTypes',
    'ShareOfCases': 'ShareOfCases',
    'BailPostedShare': 'BailPostedRatio',
    'PartialBailPostedShare': 'PartialBailPostedRatio',
    'BailNotPostedShare': 'BailNotPostedRatio',    
    'BailPosted': 'BailPostedCases',
    'PartialBailPosted': 'PartialBailPostedCases',
    'BailNotPosted': 'BailNotPostedCases',
})
mdj_race_summary = mdj_race_summary[['county', 'BailActionAuthority', "DefendantRace",
                                     'BailType', 'NumberOfCasesAllTypes', 'NumberOfCasesOfType', 'ShareOfCases',
                                      'BailActionAmtMean', 'BailActionAmtMeanCapped99th', 'BailActionAmtMedian',
                                       'BailActionAmtQ1', 'BailActionAmtQ3',
                                 'BailPostedRatio', 
                                       'BailPostedCases', 'PartialBailPostedRatio', 'PartialBailPostedCases',
                                'BailNotPostedRatio', 'BailNotPostedCases']]

In [58]:
mdj_race_summary.to_csv("mdj_race_summary.csv", index = False)

### Urbanicity

In [59]:
urbanicity_df = pd.read_csv("PA_urbanicity.csv")

In [60]:
new_df = df.merge(urbanicity_df, on = 'county', how = 'left')

In [66]:
statewide_urbanicity_summary = new_df.groupby(["urbanicity", "BailType"]).agg({
    'BailActionAmount': ['mean', mean_minus_99th_percentile, 'median', percentile(25), percentile(75)],
    'BailPosted': 'sum',
    'PartialBailPosted': 'sum',
    'BailNotPosted': 'sum',
    'OTN': 'count'
}
).reset_index()

statewide_urbanicity_summary.columns = ['_'.join(col).strip() for col in statewide_urbanicity_summary.columns.values]
statewide_urbanicity_summary.columns = [
    'urbanicity',
    'BailType',
    'BailActionAmtMean',
    'BailActionAmtMeanCapped99th',
    'BailActionAmtMedian',
    'BailActionAmtQ1',
    'BailActionAmtQ3',
    'BailPosted',
    'PartialBailPosted',
    'BailNotPosted',
    'OTN'
    
]

statewide_urbanicity_totals = new_df.groupby("urbanicity").OTN.count().reset_index()
statewide_urbanicity_totals.columns = ['urbanicity', 'total_cases']
statewide_urbanicity_summary = statewide_urbanicity_summary.merge(statewide_urbanicity_totals, on = "urbanicity", how = 'left')

statewide_urbanicity_summary['BailPostedShare'] = statewide_urbanicity_summary.BailPosted/statewide_urbanicity_summary.OTN
statewide_urbanicity_summary['PartialBailPostedShare'] = statewide_urbanicity_summary.PartialBailPosted/statewide_urbanicity_summary.OTN
statewide_urbanicity_summary['BailNotPostedShare'] = statewide_urbanicity_summary.BailNotPosted/statewide_urbanicity_summary.OTN
statewide_urbanicity_summary['ShareOfCases'] = statewide_urbanicity_summary.OTN/statewide_urbanicity_summary.total_cases
statewide_urbanicity_summary = statewide_urbanicity_summary.rename(columns= {
    'BailType': 'BailType',
    'OTN' : 'NumberOfCasesOfType',
    'total_cases' : 'NumberOfCasesAllTypes',
    'ShareOfCases': 'ShareOfCases',
    'BailPostedShare': 'BailPostedRatio',
    'PartialBailPostedShare': 'PartialBailPostedRatio',
    'BailNotPostedShare': 'BailNotPostedRatio',    
    'BailPosted': 'BailPostedCases',
    'PartialBailPosted': 'PartialBailPostedCases',
    'BailNotPosted': 'BailNotPostedCases',
})
statewide_urbanicity_summary = statewide_urbanicity_summary[['urbanicity', 'BailType', 'NumberOfCasesAllTypes', 'NumberOfCasesOfType', 'ShareOfCases',
                                      'BailActionAmtMean', 'BailActionAmtMeanCapped99th', 'BailActionAmtMedian',
                                       'BailActionAmtQ1', 'BailActionAmtQ3',
                                 'BailPostedRatio', 
                                       'BailPostedCases', 'PartialBailPostedRatio', 'PartialBailPostedCases',
                                'BailNotPostedRatio', 'BailNotPostedCases']]

In [67]:
statewide_urbanicity_summary

urbanicity     BailType  NumberOfCasesAllTypes  NumberOfCasesOfType  \
0      Rural     Monetary                  95039                35297   
1      Rural      Nominal                  95039                   59   
2      Rural  Nonmonetary                  95039                 4145   
3      Rural          ROR                  95039                19189   
4      Rural    Unsecured                  95039                36349   
5      Urban     Monetary                 288278               131002   
6      Urban      Nominal                 288278                  337   
7      Urban  Nonmonetary                 288278                20058   
8      Urban          ROR                 288278                66960   
9      Urban    Unsecured                 288278                69921   

   ShareOfCases  BailActionAmtMean  BailActionAmtMeanCapped99th  \
0      0.371395       35980.661813                 33193.597756   
1      0.000621        1807.644068                  1561.881356   
2      0.043614           0.000000                     0.000000   
3      0.201907           0.000000                     0.000000   
4      0.382464        8202.215824                  7743.248590   
5      0.454429       48712.893871                 39412.157928   
6      0.001169        3978.513769                  2123.914362   
7      0.069579           0.000000                     0.000000   
8      0.232276           0.000000                     0.000000   
9      0.242547        8614.616803                  7887.081442   

   BailActionAmtMedian  BailActionAmtQ1  BailActionAmtQ3  BailPostedRatio  \
0              15000.0           5000.0          40000.0         0.397768   
1                  1.0              1.0              1.0         0.254237   
2                  0.0              0.0              0.0         0.266586   
3                  0.0              0.0              0.0         0.224921   
4               5000.0           2500.0          10000.0         0.408044   
5              10000.0           5000.0          30000.0         0.405620   
6                  1.0              1.0              1.0         0.320475   
7                  0.0              0.0              0.0         0.020291   
8                  0.0              0.0              0.0         0.083139   
9               5000.0           2500.0          10000.0         0.393759   

   BailPostedCases  PartialBailPostedRatio  PartialBailPostedCases  \
0            14040                0.003910                     138   
1               15                0.000000                       0   
2             1105                0.002171                       9   
3             4316                0.000573                      11   
4            14832                0.000880                      32   
5            53137                0.008832                    1157   
6              108                0.005935                       2   
7              407                0.000349                       7   
8             5567                0.000105                       7   
9            27532                0.002117                     148   

   BailNotPostedRatio  BailNotPostedCases  
0            0.598323               21119  
1            0.745763                  44  
2            0.731242                3031  
3            0.774506               14862  
4            0.591075               21485  
5            0.585518               76704  
6            0.673591                 227  
7            0.979360               19644  
8            0.916756               61386  
9            0.604125               42241